In [1]:
from cpymad.madx import Madx # you can download it from github
from matplotlib import pyplot as plt
myMad = Madx()


  ++++++++++++++++++++++++++++++++++++++++++++
  +     MAD-X 5.05.01  (64 bit, Linux)       +
  + Support: mad@cern.ch, http://cern.ch/mad +
  + Release   date: 2019.06.07               +
  + Execution date: 2022.02.14 13:49:47      +
  ++++++++++++++++++++++++++++++++++++++++++++


## An introduction to MAD-X

In this first part we are going to get familiar with MAD-X syntax. This is an extension of what it is required from the tutorial.

For more information please refer to the [MAD-X online manual](http://cern.ch/madx/releases/last-rel/madxuguide.pdf).
- The lattice elements are placed along the reference orbit (variable s)
- Horizontal plane is x, and it is the bending plane
- Vertical plane is y
- Describes a local coordinate system moving along s, i.e. x=y=0 follows the curvilinear system

- MADX uses input files written in ASCII mode consisting of a sequence of statements. 

- Each statement must be terminated with a semicolon (;)

- The input is **not case sensitive** except for strings enclosed in double quotes (" ")

- Comments are indicated by (!) or (//) or (/* when a comment extends over several lines */)

- The general format of a command is:

    **label: keyword {,attribute} ;**
    
- where { } is not part of the command, and the items enclosed in the brackets can be omitted or repeated any number of times

- **label** label is the name of the stored command
    - when a command has a label, MAD-X keeps this command in memory;
    - one can repeat the execution of the same command by simply entering **EXEC label;**
- **keyword** identifies the action desired
    - keywords are protected; attempting to use a protected keyword as a label results in a fatal error
- **attributes** entered in the form: **attribute-name = attribute-value**
    - attributes serve to define data for the command
    - if a value is to be assigned to an attribute, the attribute-name is mandatory
    - attributes type:
        - string
        - logical
        - integer
        - real
        - expression
        - range
- **Variables**
    - "VAR1 = GAUSS()x1.5E-3" means VAR1 receives the current value of the expression on the right, **but does not depend on it any further**
    - "VAR1 := GAUSS()x1.5E-3" means VAR1 depends on the expression on the right, and everytime the expression changes, the variable on the left is re-evaluated, except for **const** variables
    
- Example 1: **dipole declaration**

    **mb: sbend, l=2.0, angle=2.0*pi/20;**
    
    >label = mb
    
    >keyword = sbend
    
    >atribute-name = l, attribute-value=2
    
    >atribute-name = angle, attribute-value=2.0*pi/20
    
    where l=length is in meters and angle is in rad
    
- Example 2: **quadrupole declaration**

    **QF: QUADRUPOLE, L=3.0, K1=0.0197278**
    
    where K1 is the normalized strength in m^(-2)

### Example: define a LHC dipole magnet and calculate the bending radius
- LHC dipole lenght is 14.3 m
- Dipole field is 8.33 T
- The beam momentum at 8.33 T is 7.0e12 eV

In [2]:
myString='''
length = 14.3;
B = 8.33;
PTOT = 7.0e12;
ANGLHC = B*clight * length/PTOT;
MBLHC: SBEND, L=length, ANGLE=ANGLHC;
VALUE, MBLHC->ANGLE;
'''
myMad.input(myString);

mblhc->angle       =     0.005101568258 ;


### Thick and thin elements
- Thick elements are specified with a given length
- Thin element have length=0
- Thick elements have length and strength specified separatelly (except for dipole)
- Thin elements specify **field integrals**, e.g. koL, k1L, k2L ...

### Special MAD-X elements: multipoles
- Multipole is a special elememt of zero length (thin lens)
- Examples:
    - mul0: multipole, knl={angle,0,0,....}; !This is a dipole
    - mul1: multipole, knl:={0,k1L,0,0,....}; !This is a quadrupole

### Sequence
- A MAD-X sequency assigns positions to elements
- A sequence has a name
- The position can be defined at **CENTRE** or **EXIT** or **ENTRY** of an element
- Example:

    **louvain: SEQUENCE, REFER=CENTRE,L=3000;**
    
    ....
    
    **MBL01: MBLA, at=102.7484;**
    
    **MBL02: MBLB, at=112.7484;**
    
    **MQ01: MQA, at=119.3984;**
    
    **BPM01: BPM, at=1.75, from MQ01;**
    
    **COR01: MCV01, at=LMCV/2+LBPM/2, from BPM01;**
    
    **MBL03: MBLA, at=126.3484;**
    
    **MBL04: MBLB, at=136.3484;**
    
    **MQ02: MQB, at=142.9984;**
    
    **BPM02: BPM, at=1.75, from MQ02;**
    
    **COR02: MCV02, at=LMCV/2+LBPM/2, from BPM02;**
    
    ....
    
    **ENDSEQUENCE;**

### The beam definition
- Some MAD-X calculations need to know the type of beam and properties:
    - Particle type
    - Energy
    - Emittance, number of particles, intensity
- Example:
    **BEAM, PARTICLE=proton, MASS=mass, NPART=1.1e11, CHARGE=q, ENERGY=450, ....;**

### Calculate twiss parameters
twiss;

twiss, file=my.file;

twiss, sequence=louvain;

### Look at the beta functions
plot, haxis=s, vaxis=betax, betay;

### Store selected parameters
The following command will calculate the twiss parameters around the machine but will store only the **selected** ones on file:

   **SELECT**, FLAG=twiss, **COLUMN=name,s,betx,bety**;

   twiss, sequence=louvain, file=my.file;

   plot, haxis=s, vaxis=betx, bety, colour=100;

### Survey
- The command **survey** gives the geometrical layout of the machine
- **survey, file=survey.out;**


![This is an image](survey1.png)

### How to use MAD-X
- Define the input, i.e. the elements and the sequence (it's more elegant to have two files, one for the elements description and one for the sequence)
- Define the beam
- Make the computations (twiss calculation, error assignment, orbit correction, etc)
- Analyse the output results
- Match desired parameters

## An introduction to CPYMAD
For more information please refer to the [cpymad online manual](http://hibtc.github.io/cpymad/getting-started.html#basic-mad-x-commands)

The basic way to use cpymad is to create a Madx instance that can be used to control and access the state of a MAD-X process:

*from cpymad.madx import Madx*

*mymad = Madx()* 

**mymad** is now our Madx instance

Most MAD-X commands can be executed using the corresponding method on the Madx instance, for example:

- Reading a file:
    - MADX-X: **CALL, FILE = 'my.file';**
    - CPYMAD: *mymad.call(file='my.file')*
- Executing twiss:
    - MAD-x:
        **TWISS, SEQUENCE=LEBT, BETX=0.1, BETY=0.1, ALFX=0.1, ALFY=0.1;** 
    - CPYMAD:
        *mytwiss = mymad.twiss(sequence='LEBT',betx=0.1, bety=0.1,alfx=0.1, alfy=0.1)*
        
        twiss(): returns the resulting twiss table (here *mytwiss*), which can be used conveniently for your own analysis
        
        For example, plotting the twiss parameters using the matplotlib
        
        *import matplotlib.pyplot as plt*
        
        *plt.plot(mytwiss.s, mytwiss.betx)*
        
        *plt.show()*
- More simple: input()
    - The method responsible for feeding textual input to MAD-X is input() method. 
    - It is called with a single string argument that will be forwarded as input to the MAD-X interpreter. 
    - For example: *madx.input('CALL, FILE='my.file';')*
- command()
    - Define a beam:
        - *madx.command.beam(sequence='LEBT', particle='PROTON')*
    - Declare lattice elements:
        - *madx.command.quadrupole.clone('QF', L=3.0, K1=0.0197278)*

In [1]:
from cpymad.madx import Madx # you can download it from github
from matplotlib import pyplot as plt
myMad = Madx()


  ++++++++++++++++++++++++++++++++++++++++++++
  +     MAD-X 5.05.01  (64 bit, Linux)       +
  + Support: mad@cern.ch, http://cern.ch/mad +
  + Release   date: 2019.06.07               +
  + Execution date: 2022.01.13 15:22:11      +
  ++++++++++++++++++++++++++++++++++++++++++++


In [2]:
myString='''
stop;
'''
myMad.input(myString);


  Number of warnings: 0

  ++++++++++++++++++++++++++++++++++++++++++++
  +          MAD-X finished normally         +
  ++++++++++++++++++++++++++++++++++++++++++++


With the 'stop;' instruction we exit from MAD-X, so, as done in the following cell we need to re-istantiate our MAD-X object with the 
**myMad = Madx()** instruction.

---
It is a good practice to make header, please use '!' to comment the single line.

In [4]:
myString='''
!***************************************
! It is a good practice to make a header
!***************************************
title,'My test'; 
value, title;
'''
myMad.input(myString);

---
Print the version of MAD-X

In [5]:
myString='''
value, VERSION;
'''
myMad.input(myString);

version            =              50601 ;


--- 
Use the **help** keyword (very rudimental help)

In [6]:
myString='''
help, beam;
'''
myMad.input(myString);

command: beam  module: control
parameter: particle   string: positron
parameter: sequence   string: (null)
parameter: bunched   logical: true
parameter: radiate   logical: false
parameter: mass   expression: emass :: value:      0.00051099895
double value:      0.00051099895
parameter: charge   double value:                  1
parameter: energy   double value:                  1
parameter: pc   double value:                  0
parameter: gamma   double value:                  0
parameter: beta   double value:                  0
parameter: brho   double value:                  0
parameter: ex   double value:                  1
parameter: exn   double value:                  0
parameter: ey   double value:                  1
parameter: eyn   double value:                  0
parameter: et   double value:              0.001
parameter: sigt   double value:                  1
parameter: sige   double value:              0.001
parameter: kbunch   double value:                  1
parameter: np

---
This is an example to make a system call, just for showing you how to do it. The system call string (in this case 'pwd') depends on the Operating System.

In [7]:
myString='''
system,'date';
'''
myMad.input(myString);


Tue Nov 23 17:15:41 CET 2021


### Example: define a LHC dipole magnet and calculate the bending radius
- LHC dipole lenght is 14.3 m
- Dipole field is 8.33 T
- The beam momentum at 8.33 T is 7.0e12 eV

In [2]:
myString='''
length = 14.3;
B = 8.33;
PTOT = 7.0e12;
ANGLHC = B*clight * length/PTOT;
MBLHC: SBEND, L=length, ANGLE=ANGLHC;
VALUE, MBLHC->ANGLE;
'''
myMad.input(myString);

mblhc->angle       =     0.005101568258 ;


---
This is an example to get familiar with the use of the physical constants and the formatting of the output. Have a look on the difference.

In [8]:
myString='''
a=pi;
value a; 
set, format="22.20e";
value a; 
! reset to nominal values
option,reset=True;
set, format="10d", "18.10g", "-18s";
'''
myMad.input(myString);

---
This is an example to get familiar with **if** and deferred expression. Please note the after the block delimited with **{...}** the **;** can be omitted. Pay attention to circular call!

In [9]:
myString='''
if (1==1){
option, echo=false, info=true;
a=pi;
b:=a;
c=a;
value a; 
value b;
value c;
a=CLIGHT*cos(a);
value a;
value b;
value c;}
! BEWARE of circular call!
!a:=a+1;
! When evaluating you will get a fatal error
! value a; 
option, echo=true, info=true;
'''
myMad.input(myString);

+++ memory access outside program range, fatal +++


RuntimeError: MAD-X has stopped working!

---
This is an example to get familiar with **while** and **macros** loops.

In [ ]:
myString='''
a(myvariable1,myvariable2): macro = {
value, myvariable1;
value, myvariable1*myvariable2;
}

N=1;
while (N<10){
exec, a(N,N);
N=N+1;
}
'''
myMad.input(myString);

---
### List of functions
In MAD-X the following functions are available

- SQRT(x) square root,
- LOG(x) natural logarithm,
- LOG10(x) logarithm base 10,
- EXP(x) exponential,
- SIN(x) trigonometric sine,
- COS(x) trigonometric cosine,
- TAN(x) trigonometric tangent,
- ASIN(x) arc sine,
- ACOS(x) arc cosine,
- ATAN(x) arc tangent,
- SINH(x) hyperbolic sine,
- COSH(x) hyperbolic cosine,
- TANH(x) hyperbolic tangent,
- SINC(x) cardinal sine function,
- ABS(x) absolute value,
- ERF(x) Gauss error,
- ERFC(x) complementary error,
- FLOOR(x) floor, largest previous integer,
- CEIL(x) ceiling, smallest next integer,
- ROUND(x) round, closest integer,
- FRAC(x) fractional part of number,
- RANF() random number, uniformly distributed in [0,1],
- GAUSS() random number, gaussian distribution with unit standard deviation,
- TGAUSS(x) random number, gaussian distribution with unit standard deviation, truncated at x standard deviations;

In [ ]:
myString='''
value, 1+1.2;
value, 1-1.2;
value, 1*1.2;
value, 1/1.2;
value, 2^0.5;
value, 1/0;
value, 2^-0.5;
value, sqrt(3);
value, log(10);
value, log10(10^2);
value, exp(0);
value, sin(pi/2);
value, cos(sqrt(2)/2);
value, tan(pi/2);
value, asin(0);
value, acos(0);
value, atan(0);
value, sinh(pi/2);
value, cosh(sqrt(2)/2);
value, tanh(pi/2);
value, sinc(0);
value, abs(-1.2);
value, erf(1);
value, 1-erfc(1);
value, ceil(2.3);
value, round(2.3);
value, frac(2.3);
value, ranf();
value, gauss();
value, tgauss(.1);
'''
myMad.input(myString)

---
### List of physical constant

| MAD-X name  | symbol  |  value |unit|
|:-:|:-:|:-:|:-:|
|PI| π |4 * atan(1)| 1|
|TWOPI|2π| 2 * PI| 1|
|DEGRAD| 180/π |180 / PI| deg/rad|
|RADDEG| π/180 |PI / 180 |rad/deg|
|E| e |exp(1) |1|
|EMASS| me |0.510998928e−3| GeV|
|PMASS| mp |0.938272046| GeV|
|NMASS| u |0.931494061| GeV|
|MUMASS| mµ| 0.1056583715 |GeV|
|CLIGHT| c| 299792458| m/s|
|QELECT| e| 1.602176565e−19| A.s|
|HBAR| ¯h| 6.58211928e−25| MeV.s|
|ERAD| re| 2.8179403267e−15| m|
|PRAD| re(me/mp)| ERAD*EMASS/PMASS| m|


In [ ]:
myString='''
value, pi;
value, twopi;
value, raddeg;
value, degrad;
value, e;
value, emass;
value, pmass;
value, nmass;
value, mumass;
value, clight;
value, qelect;
value, hbar;
value, erad;
value, prad;
'''
myMad.input(myString)

---
### Inheritance and *->* operator

In [10]:
myString='''
a: drift, l=2;
b: a;
a->l=3;
value, a->l;
value, b->l;
'''
myMad.input(myString)

RemoteProcessClosed: 